In [ ]:
%load_ext autoreload
%autoreload 2

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
!pip install optuna optuna-dashboard
!pip install git+https://github.com/R-N/ml-utility-loss
!pip install git+https://github.com/R-N/ml-utility-loss --force-reinstall --no-deps

  Cloning https://github.com/R-N/ml-utility-loss to /tmp/pip-req-build-u7i3t6eu
  Running command git clone --filter=blob:none --quiet https://github.com/R-N/ml-utility-loss /tmp/pip-req-build-u7i3t6eu
  Resolved https://github.com/R-N/ml-utility-loss to commit e9512918d69ed70bcd15f1c49c3e237aef190374
  Preparing metadata (setup.py) ... done
  Cloning https://github.com/R-N/ml-utility-loss to /tmp/pip-req-build-x60ffe6m
  Running command git clone --filter=blob:none --quiet https://github.com/R-N/ml-utility-loss /tmp/pip-req-build-x60ffe6m
  Resolved https://github.com/R-N/ml-utility-loss to commit e9512918d69ed70bcd15f1c49c3e237aef190374
  Preparing metadata (setup.py) ... done
  Created wheel for ml-utility-loss: filename=ml_utility_loss-0.1.1-py3-none-any.whl size=378135 sha256=3a86f84ff278165130abf3a6f7bb9388a0377e9c13393abc27d261f32187fb33
  Stored in directory: /tmp/pip-ephem-wheel-cache-6thuu3xt/wheels/54/30/38/31c28079b5f07b6c793211d38f72e7f0be6764bfdfe016df74
Successfully buil

In [ ]:
%cd /content
!curl -Ls https://github.com/ekzhang/bore/releases/download/v0.4.0/bore-v0.4.0-x86_64-unknown-linux-musl.tar.gz | tar zx -C /usr/bin
!curl -Lo /usr/bin/cloudflared https://github.com/cloudflare/cloudflared/releases/latest/download/cloudflared-linux-amd64 && chmod +x /usr/bin/cloudflared

/content
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
100 34.7M  100 34.7M    0     0  13.1M      0  0:00:02  0:00:02 --:--:-- 17.5M


In [ ]:
%cd /content
!rm -rf ml-utility-loss
!git clone https://github.com/R-N/ml-utility-loss
%cd ml-utility-loss
!rm -rf ml_utility_loss

/content
Cloning into 'ml-utility-loss'...
remote: Enumerating objects: 54455, done.
remote: Counting objects: 100% (7368/7368), done.
remote: Compressing objects: 100% (3271/3271), done.
remote: Total 54455 (delta 4163), reused 7285 (delta 4081), pack-reused 47087
Receiving objects: 100% (54455/54455), 239.42 MiB | 10.83 MiB/s, done.
Resolving deltas: 100% (6211/6211), done.
Updating files: 100% (50325/50325), done.
/content/ml-utility-loss


In [ ]:
datasets = [
    "insurance",
    "treatment",
    "contraceptive"
]

model_dir = "/content/drive/MyDrive/rizqinur2010/Documents/ITS/Tesis/Model/"

In [ ]:
import pandas as pd
import numpy as np
import json
import os

dataset_dir = "datasets"
dataset_name = "treatment"

df = pd.read_csv(os.path.join(dataset_dir, f"{dataset_name}.csv"))
with open(os.path.join(dataset_dir, f"{dataset_name}.json")) as f:
    info = json.load(f)

In [ ]:
from ml_utility_loss.util import split_df_ratio

task = info["task"]
target = info["target"]
cat_features = info["cat_features"]
mixed_features = info["mixed_features"]
longtail_features = info["longtail_features"]
integer_features = info["integer_features"]

dfs = {
    "df": df,
}
dfs_test = {}
for i in range(5):
    train, test = split_df_ratio(df, ratio=0.2, i=i, seed=42)
    dfs[i] = train
    dfs_test[i] = test


In [ ]:
from ml_utility_loss.util import mkdir

model_name = "realtabformer"
df_name = 3
#model_name_2 = f"{model_name}_{dataset_name}_{df_name}"
model_dir_2 = os.path.join(model_dir, model_name, dataset_name, str(df_name))
mkdir(model_dir_2)
params_path = os.path.join(model_dir_2, f"params.json")

In [ ]:
print(model_dir_2)

/content/drive/MyDrive/rizqinur2010/Documents/ITS/Tesis/Model/realtabformer/treatment/3


In [ ]:

from ml_utility_loss.tuning import create_objective
import ml_utility_loss.synthesizers.realtabformer.params as PARAMS
from ml_utility_loss.util import filter_dict_2, filter_dict
from copy import deepcopy

params = getattr(PARAMS, dataset_name).BEST

model_params={
    **params,
}

model_params["epochs"] = min(model_params.pop("epochs", 100), 100)

model_params_ = deepcopy(model_params)

In [ ]:
from ml_utility_loss.synthesizers.realtabformer.wrapper import REaLTabFormer
from ml_utility_loss.synthesizers.realtabformer.params.default import GPT2_PARAMS, REALTABFORMER_PARAMS

from transformers.models.gpt2 import GPT2Config

train = dfs[df_name]

num_bootstrap = model_params.pop("num_bootstrap", 100)

gpt2_params = filter_dict(model_params, GPT2_PARAMS)
realtabformer_params = filter_dict(model_params, REALTABFORMER_PARAMS)

# Non-relational or parent table.
rtf_model = REaLTabFormer(
    tabular_config=GPT2Config(**gpt2_params),
    **realtabformer_params
)

rtf_model.experiment_id = str(df_name)
rtf_model.fit(
    train,
    num_bootstrap=num_bootstrap
)

synth_df = rtf_model.sample(n_samples=len(train))

Computing the sensitivity threshold...


/usr/local/lib/python3.10/dist-packages/ml_utility_loss/synthesizers/realtabformer/wrapper.py:184: UserWarning: The `bos_token_id`, `eos_token_id`, and `vocab_size` attributes will                     be replaced when the `.fit` method is run.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/ml_utility_loss/synthesizers/realtabformer/wrapper.py:400: UserWarning: Duplicate rate (0.0) in the data is zero. The `qt_interval` will be set                     to qt_interval_unique=100.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/ml_utility_loss/synthesizers/realtabformer/wrapper.py:427: UserWarning: qt_interval adjusted from 100 to 21...
  warnings.warn(


Bootstrap round:   0%|          | 0/100 [00:00<?, ?it/s]

Sensitivity threshold summary:
count    100.000000
mean       0.000021
std        0.004963
min       -0.010845
25%       -0.003834
50%        0.000164
75%        0.003828
max        0.012331
dtype: float64
Sensitivity threshold: 0.007889908256880733 qt_max: 0.05


  0%|          | 0/1308 [00:00<?, ?it/s]

...

69
69
69
69
69
69
69
69
69
69
69
Generated 0 invalid samples out of total 1408 samples generated. Sampling efficiency is: 100.0000%
Saving not-best model...
Critic round: 35,                     sensitivity_threshold: 0.007889908256880733,                         val_sensitivity: 0.0095012378039901,                             val_sensitivities: [0.007153778942769769, 0.007328527741371779, 0.007219309742245524, 0.01490825688073395, 0.011063783311489736, 0.015607252075141983, 0.010889034512887728, 0.014667977282656184, 0.006323722149410225, 0.016131498470948014, 0.004161205766710354, 0.009927916120576672, 0.003287461773700307, 0.0036588029707295766, 0.010190039318479685]


  0%|          | 0/1308 [00:00<?, ?it/s]

69
69
69
69
69
69
69
69
69
69
69
Generated 0 invalid samples out of total 1408 samples generated. Sampling efficiency is: 100.0000%
Critic round: 40,                     sensitivity_threshold: 0.007889908256880733,                         val_sensitivity: 0.019852191641182466,                             val_sensitivities: [0.024126256006989952, 0.01980122324159022, 0.022990388816076894, 0.028844473569244213, 0.031684141546526864, 0.0222258628221931, 0.018272171253822633, 0.01947356924421145, 0.011762778505897771, 0.021373962429008304, 0.01147881170816951, 0.020915246832678026, 0.014820882481432943, 0.014733508082131934, 0.015279598077763221]
Stopping training, no improvement in critic...


  0%|          | 0/2648 [00:00<?, ?it/s]

69
69
69
69
69
69
69
69
69
69
69
69
69
69
69
69
69
69
69
69
69
Generated 0 invalid samples out of total 2688 samples generated. Sampling efficiency is: 100.0000%


In [ ]:
import torch
from copy import deepcopy
import json
import locale
locale.getpreferredencoding = lambda: "UTF-8"

rtf_model.experiment_id = str(df_name)
rtf_model.save(model_dir_2)
!rm -rf {model_dir_2}/{df_name}/not-best-disc-model
!rm -rf {model_dir_2}/{df_name}/last-epoch-model
!rm -rf {model_dir_2}/{df_name}/rtf_model.pt
with open(params_path, "w") as f:
    json.dump(model_params_, f, indent=4)

Copying artefacts from: best-disc-model
Copying artefacts from: mean-best-disc-model
Copying artefacts from: not-best-disc-model
Copying artefacts from: last-epoch-model


In [ ]:
!ls {model_dir_2}/{df_name}

best-disc-model  mean-best-disc-model  rtf_config.json


In [ ]:
synth_path = os.path.join(model_dir_2, f"synth.csv")
train_path = os.path.join(model_dir_2, f"train.csv")
val_path = os.path.join(model_dir_2, f"val.csv")
test_path = os.path.join(model_dir_2, f"test.csv")

synth_df.to_csv(synth_path)
dfs[df_name].to_csv(train_path)
dfs_test[df_name].to_csv(val_path)
dfs_test[df_name].to_csv(test_path)